## XBRL US API - FERC schedule by entity  

### Authenticate for access token 
Click in the gray code cell below, then click the Run button above to execute the cell. Type your XBRL US Web account email, account password, Client ID, and secret as noted, pressing the Enter key on the keyboard after each entry.

XBRL US limits records returned for a query to improve efficiency; this script loops to collect all data from the Public Filings Database for a query. **Non-members might not be able to return all data for a query** - join XBRL US for comprehensive access - https://xbrl.us/join.

In [ ]:
print('Enter your XBRL US Web account email: ')
import os, re, sys, json
import requests
import pandas as pd
from IPython.display import display, HTML
import numpy as np
import getpass
from datetime import datetime
import urllib
from urllib.parse import urlencode
email = input()
password = getpass.getpass(prompt='Password: ')
clientid = getpass.getpass(prompt='Client ID: ')
secret = getpass.getpass(prompt='Secret: ')

body_auth = {'username' : ''.join(email), 
            'client_id': ''.join(clientid), 
            'client_secret' : ''.join(secret), 
            'password' : ''.join(password), 
            'grant_type' : 'password', 
            'platform' : 'ums-ipynb' }

payload = urlencode(body_auth)
url = 'https://api.xbrl.us/oauth2/token'
headers = {"Content-Type": "application/x-www-form-urlencoded"}

res = requests.request("POST", url, data=payload, headers=headers)
auth_json = res.json()

if 'error' in auth_json:
    print ("\n\nThere was a problem generating an access token with these credentials. Run the first cell again to enter credentials.")
else:
    print ("\n\nYour access token expires in 60 minutes. After it expires, run the cell immediately below this one to generate a new token and continue to use the query cell. \n\nFor now, skip ahead to the section 'Make a Query'.")
access_token = auth_json['access_token']
refresh_token = auth_json['refresh_token']
newaccess = ''
newrefresh = ''
#print('access token: ' + access_token + ' refresh token: ' + refresh_token)

#### Refresh token 
The cell below is only needed to refresh an expired access token after 60 minutes. When the access token no longer returns results, run the cell below to refresh the access token or re-enter credentials by running the cell above. Until the refresh token process is needed, **skip ahead to _Make a Query_**. 


In [ ]:
token = token if newrefresh != '' else refresh_token 

refresh_auth = {'client_id': ''.join(clientid), 
            'client_secret' : ''.join(secret), 
            'grant_type' : 'refresh_token', 
            'platform' : 'ipynb', 
            'refresh_token' : ''.join(token) }
refreshres = requests.post(url, data=refresh_auth)
refresh_json = refreshres.json()
access_token = refresh_json['access_token']
refresh_token = refresh_json['refresh_token']#print('access token: ' + access_token + 'refresh token: ' + refresh_token)
print('Your access token is refreshed for 60 minutes. If it expires again, run this cell to generate a new token and continue to use the query cells below.')
print(access_token)

### Make a query 
After the access token confirmation appears above, you can modify the query below and use the **_Cell >> Run_** menu option with the cell **immediately below this text** to run the query for updated results. 

The sample results are from 10+ years of data for companies filing data on the _Summary of Utility Plant and Accumulated Provisions for Depreciation, Amortization and Depletion_ , and may take several minutes to recreate.  

Modify the **_XBRL\_Elements_** to return data from a different FERC Form 1 Schedule, and/or change the **_entity\_codes_** to shorten the list. You can also change the base taxonomy corresponding to the Form by year or Form type. The queries to get lists are in the commented lines above each variable.
  
Refer to XBRL API documentation at https://xbrlus.github.io/xbrl-api/#/Facts/getFactDetails for other endpoints and parameters to filter and return. 

In [ ]:
# Define the parameters for the filter and fields to be returned, 
# run the loop to return results
offset_value = 0
res_df = []

# Define the parameters of the query

# query all taxonomies published for a specific year
# https://api.xbrl.us/api/v1/dts/search?fields=dts.id,dts.version.sort(DESC),dts.taxonomy-name.sort(DESC)&dts.version=2023

# query unique Statements in the 2023 FERC Form 1 Taxonomy
# https://api.xbrl.us/api/v1/dts/730705/network/search?network.link-name=presentationLink&fields=network.role-description.sort(ASC),dts.id&unique

XBRL_Elements = ["200 - Schedule - Summary of Utility Plant and Accumulated Provisions for Depreciation, Amortization and Depletion"]

# query for a list of Form 1 filer entity codes:
# https://api.xbrl.us/api/v1/report/search?report.document-type=1&fields=report.entity-name.sort(ASC),entity.code&unique
entity_codes = [
'C000533','C001111' 
]

# Define data fields to return (multi-sort based on order)

fields = [ # this is the list of the characteristics of the data being returned by the query
		'period.fiscal-year.sort(DESC)',
		'period.fiscal-period.sort(DESC)',
		'entity.code',
		'report.entity-name',
		'report.id',
		'cube.description.sort(ASC)',
		'cube.tree-sequence.sort(ASC)',
		'cube.primary-local-name',
		'fact.value',
		'unit',
		'dimensions.count',
		'dimension-pair.sort(ASC)'
        ]

params = { # this is the list of what's being queried against the search endpoint
         'cube.description': ','.join(XBRL_Elements),  
         'entity.code': ','.join(entity_codes),
         # uncomment this line to run by report.id AND comment the prior line for entity.code 'report.id': ','.join(full_list),
         'fields': ','.join(fields)
         }

endpoint = 'cube'

# Execute the query with loop for all results - do not edit below this line

search_endpoint = 'https://api.xbrl.us/api/v1/' + endpoint + '/search'
orig_fields = params['fields']

count = 0
query_start = datetime.now()
printed = False
while True:
    if not printed:
        printed = True
    res = requests.get(search_endpoint, params=params, headers={'Authorization' : 'Bearer {}'.format(access_token)})
    res_json = res.json()
    if 'error' in res_json:
        print('There was an error: {}'.format(res_json['error_description']))
        break

    print("up to", str(offset_value + res_json['paging']['limit']), "records are found so far ...")

    res_df += res_json['data']

    if res_json['paging']['count'] < res_json['paging']['limit']:
        print(" - this set contained fewer than the", res_json['paging']['limit'], "possible, only", str(res_json['paging']['count']), "records.")
        break
    else: 
        offset_value += res_json['paging']['limit'] 
        if 100 == res_json['paging']['limit']:
                params['fields'] = orig_fields + ',' + endpoint + '.offset({})'.format(offset_value)
                if offset_value == 10 * res_json['paging']['limit']:
                        break 
        elif 500 == res_json['paging']['limit']:
                params['fields'] = orig_fields + ',' + endpoint + '.offset({})'.format(offset_value)
                if offset_value == 4 * res_json['paging']['limit']:
                        break 
        params['fields'] = orig_fields + ',' + endpoint + '.offset({})'.format(offset_value)

if not 'error' in res_json:
    current_datetime = datetime.now().replace(microsecond=0)
    time_taken = current_datetime - query_start
    index = pd.DataFrame(res_df).index
    total_rows = len(index)
    your_limit = res_json['paging']['limit']
    limit_message = "If the results below match the limit noted above, you might not be seeing all rows, and should consider upgrading (https://xbrl.us/access-token).\n"
    
    if your_limit == 100:
        print("\nThis non-Member account has a limit of " , 10 * your_limit, " rows per query from our Public Filings Database. " + limit_message)
    elif your_limit == 500:
        print("\nThis Basic Individual Member account has a limit of ", 4 * your_limit, " rows per query from our Public Filings Database. " + limit_message)
    
    print("\nAt " + current_datetime.strftime("%c") +  ", the query finished with  ", str(total_rows), "  rows returned in " + str(time_taken) + " for \n" +  urllib.parse.unquote(res.url))
    
    
    df = pd.DataFrame(res_df)
    # the format truncates the HTML display of numerical values to two decimals; .csv data is unaffected
    pd.options.display.float_format = '{:,.2f}'.format
    display(HTML(df.to_html()))

up to 5000 records are found so far ...
 - this set contained fewer than the 5000 possible, only 4534 records.

At Tue Jul 25 16:02:04 2023, the query finished with   4534   rows returned in 0:00:00.410091 for 
https://api.xbrl.us/api/v1/cube/search?cube.description=200+-+Schedule+-+Summary+of+Utility+Plant+and+Accumulated+Provisions+for+Depreciation,+Amortization+and+Depletion&entity.code=C000533,C001111&fields=period.fiscal-year.sort(DESC),period.fiscal-period.sort(DESC),entity.code,report.entity-name,report.id,cube.description.sort(ASC),cube.tree-sequence.sort(ASC),cube.primary-local-name,fact.value,unit,dimensions.count,dimension-pair.sort(ASC)


In [ ]:
# If you run this program locally, you can save the output to a file on your computer (modify D:\results.csv to your system)
df.to_csv(r"D:\results.csv",sep=",")